In [2]:
import pandas  as pd 
from itertools import product
from collections import defaultdict
from itertools import groupby
from copy import deepcopy
import os
import csv
import ast
import re

Estado actual: 
* Pandas es muy lento para lo que quiero hacer
* Trabajo actual: separar los desempates en: Primero wins, despues rounds, despues mapas (probablemente no se implemente)
* Potenciales soluciones: Cambiar la manera de armar la tabla a Numpy (deberia ser lo mas rapido por mucho) Ventajas: velocidad y puedo evaluar por filas los resultados 

-------------------------------------------------------------------------

Arranco casi de 0, problemas con la unicacion de memoria de los objetos y se armo un re quilombo. 
Intento 2 diseño enfocado tabla final que tengo y estructurar desde ese punto hacia atras. 

-------------------------------------------------------------------------

24-1-25
Funcionando en trabajo por lotes. 
Dificultades actuales ordenar los batch para procesarlos. Resto de las funcionalidades parecen ok 


In [3]:
#Esto es raro, siento que estoy dando vueltas en circulo con este diccionario creando los objetos y volviendo a usarlos 
#Lo termino usando con un zip, lo que puede ser peligroso con el orden y las keys
#Agregar h2h ganados aca, voy a tener que modificar como funcionan las fuciones 
teamNameScores = {
                "name": ["Kru","Lev","100T","mibr","NRG","EG","FUR","LOUD", "2G","G2","C9","SEN"],
                "wins": [6,9,5,1,4,4,3,4,7,00,6,6],
                "loss":[4,1,5,9,6,6,7,6,3,00,4,4],
                "matchWins" : [15,19,12,3,10,10,8,11,15,00,13,13],
                "matchLoss" : [10,4,11,18,13,15,15,14,8,00,13,8],
                "roundWin":[287,296,255,168,238,241,195,249,249,00,270,249],
                "roundLoss":[247,204,232,257,237,281,270,275,214,00,276,214],
                'h2h' : [['FUR','mibr','EG','LOUD','C9','SEN'],
                         ['SEN','NRG','G2','100T','EG','LOUD','FUR'],
                         ['EG','G2','NRG'],
                         ['EG'],
                         ['Kru','LOUD','FUR','mibr'],
                         ['SEN','LOUD'],
                         ['100T','mibr'],
                         ['SEN','G2','mibr','100T'],
                         ['FUR','EG','mibr','Kru','NRG','Kru','SEN'],
                         [], 
                         ['Lev','EG','LOUD','FUR','mibr','NRG'],
                         ['100T','mibr','FUR','NRG']
                         ]
                  }

roundMatches = {
                "week11" : [["Kru","Lev"], ["100T","mibr"],["NRG","EG"], ["FUR","LOUD"],["2G","G2"],["C9","SEN"]],
                "week12" : [["Kru","100T"], ["Lev","mibr"],["NRG","FUR"], ["EG","LOUD"],["C9","G2"],["2G","SEN"]]
                }

In [14]:
#Entry vacia para checkear creacion 
teamNameScores = {
    "name": [
        "Kru",
        "Lev",
        "100T",
        "mibr",
        "NRG",
        "EG",
        "FUR",
        "LOUD",
        "2G",
        "GAMERS2",
        "C9",
        "SEN",
    ],
    "wins": [0, 0, 0, 0, 0, 0, 0, 0, 0, 00, 0, 0],
    "loss": [0, 0, 0, 0, 0, 0, 0, 0, 0, 00, 0, 0],
    "matchWins": [0, 0, 0,0, 0, 0,0, 0, 0, 0, 0, 0],
    "matchLoss": [0,0, 0, 0, 0, 0, 0, 0,0, 0, 0, 0],
    "roundWin": [0, 0, 0, 0, 0, 0, 0, 0, 0,0, 0, 0],
    "roundLoss": [0, 0, 0, 0, 0, 0, 0, 0, 0,0, 0, 0],
}

roundMatches = {
    "week11": [
        ["Kru", "Lev"],
        ["100T", "mibr"],
        ["NRG", "EG"],
        ["FUR", "LOUD"],
        ["2G", "GAMERS2"],
        ["C9", "SEN"],
    ],
    "week12": [
        ["Kru", "100T"],
        ["Lev", "mibr"],
        ["NRG", "FUR"],
        ["EG", "LOUD"],
        ["C9", "GAMERS2"],
        ["2G", "SEN"],
    ],
}

In [4]:
def process_for_round(teams):
    previous_results = []
    for i, team in enumerate(teams["name"]):
        temp_dict = {
            "UP": 1,
            "Team": team,
            "wins": teams["wins"][i],
            "matchDelta": teams["matchWins"][i] - teams["matchLoss"][i],
            "h2h": teams['h2h'][i]
        }
        previous_results.append(temp_dict)
    return previous_results

In [5]:
def run_round_delta_with_resume(matches, previous_results, batch_size=512, output_file="results_part", progress_file="progress.txt"):
    match_outcomes = list(product([0, 1, 2, 3], repeat=len(matches)))
    result_mapping = {
        0: (0, 2),
        1: (1, 2),
        2: (2, 1),
        3: (2, 0),
    }

    test_group = defaultdict(list)
    for result in previous_results:
        test_group[result["UP"]].append(result)

    # Leer el progreso guardado
    start_batch = 0
    if os.path.exists(progress_file):
        with open(progress_file, "r") as f:
            start_batch = int(f.read().strip())

    total_batches = len(match_outcomes) // batch_size + 1

    for batch in range(start_batch, total_batches):
        batch_outcomes = match_outcomes[batch * batch_size: (batch + 1) * batch_size]
        new_results = []

        for up, group in test_group.items():
            simul_teams = {
                team_data["Team"]: {
                    "wins": team_data["wins"],
                    "matchDelta": team_data["matchDelta"],
                    'h2h': team_data['h2h']
                }
                for team_data in group
            }

            for combination in batch_outcomes:
                temp_teams = deepcopy(simul_teams)

                for match_index, result in enumerate(combination):
                    team1, team2 = matches[match_index]
                    team1_score, team2_score = result_mapping[result]
                    delta_score = abs(team1_score - team2_score)

                    if result in [2, 3]:
                        temp_teams[team1]["wins"] += 1
                        temp_teams[team1]["matchDelta"] += delta_score
                        temp_teams[team2]["matchDelta"] -= delta_score
                        temp_teams[team1]["h2h"] += [team2]
                    else:
                        temp_teams[team2]["wins"] += 1
                        temp_teams[team2]["matchDelta"] += delta_score
                        temp_teams[team1]["matchDelta"] -= delta_score
                        temp_teams[team2]["h2h"] += [team1]

                new_up = f"{up}-{batch}-{combination}"

                for team, data in temp_teams.items():
                    new_results.append({
                        "UP": new_up,
                        "Team": team,
                        "wins": data["wins"],
                        "matchDelta": data["matchDelta"],
                        'h2h': data['h2h']
                    })

        # Guardado resultados parciales
        output_file_batch = output_file+str(batch)+'.csv'
        df = pd.DataFrame(new_results)
        file_exists = os.path.exists(output_file_batch) and os.path.getsize(output_file_batch) > 0
        df.to_csv(output_file_batch, mode='a', index=False, header=not file_exists)

        # Guardado del progreso
        with open(progress_file, "w") as f:
            f.write(str(batch + 1))

        print(f"Lote {batch + 1}/{total_batches} procesado y guardado.")

    print("Procesamiento completado.")
    os.remove(progress_file) #borrar el progreso si termino de procesar todo 

In [6]:
def groupby_UP(matchresults) -> list:
    group_result = defaultdict(list)
    for result in matchresults:
        group_result[result["UP"]].append(result)
    return group_result


def group_table(teamDict) -> list:
    return [list(group) for _, group in groupby(teamDict, key=lambda x: x[1]["wins"])]


def heriarchy_dict_for_sort(groupby_up_dict: dict) -> dict:
    hierarchy_dict_to_return = {}
    for key in groupby_up_dict.keys():
        hierarchy_dict_to_append = {}
        for team in groupby_up_dict[key]:
            hierarchy_dict_to_append[team["Team"]] = {
                "wins": team["wins"],
                "matchDelta": team["matchDelta"],
                "h2h": team["h2h"],
            }
        hierarchy_dict_to_return[key] = hierarchy_dict_to_append
    return hierarchy_dict_to_return


def sort_dict_by_wins(single_up_round) -> list:
    count = 1  # Esto se puede sacar ?
    sorted_table = sorted(
        single_up_round.items(),
        key=lambda x: (x[1]["wins"], x[1]["matchDelta"]),
        reverse=True,
    )
    grouped_table = group_table(sorted_table)
    count += 1  # Esto se puede sacar ?
    return grouped_table


# Tiebreak Rules
def two_teams_tie(
    tie_teams: list,
) -> (
    list
):  # Esta es rara, falla en tablas incompletas (pueden no haber jugado los dos equipos, pero no deberia falla en la ultima ronda)
    if len(tie_teams) != 2:
        print("not 2 tie teams")
    else:
        team1_h2h_vs_rival = set(tie_teams[0][1]["h2h"]) & set([tie_teams[1][0]])

        if len(team1_h2h_vs_rival) == 0:
            tie_teams = tie_teams[1:] + tie_teams[:1]
    return tie_teams


def three_way_tie(tie_teams: list) -> list:
    if len(tie_teams) != 3:
        print("not 3 way tie")
    else:
        teams = [x[0] for x in tie_teams]
        for index, team in enumerate(tie_teams):  # one team superiority vs the other 2
            team_h2h = set(tie_teams[index][1]["h2h"]) & set(teams)

            if len(team_h2h) == 2:
                pop_team = tie_teams.pop(index)
                remaining_tie = two_teams_tie(tie_teams)
                tie_teams = [pop_team] + remaining_tie

            elif index == 2:
                print("Round diff needed")
    return tie_teams


def tiebreaker(tie_teams):
    amount_tie_teams = len(tie_teams)
    if amount_tie_teams >= 4:
        match_tie_set = set()
        for team in tie_teams:  # This need to be check
            match_tie_set.add(team[1]["matchDelta"])
        if amount_tie_teams != match_tie_set:
            pass

    if amount_tie_teams == 3:
        tie_teams = three_way_tie(tie_teams)

    if amount_tie_teams == 2:  # Esto se puede cambiar y modificar solo la posición
        tie_teams = two_teams_tie(tie_teams)

    return tie_teams or []

In [7]:
def untie_round_save(up_dict_sorted,dict_up_position, key):
    positon = 1
    return_dict = []
    for list_team in up_dict_sorted:
        if len(list_team) == 1:                  
            dict_up_position[list_team[0][0]][str(positon)][0] += 1
            dict_up_position[list_team[0][0]][str(positon)][1].add(key)
            positon += 1
            return_dict += [list_team]
        if len(list_team) > 1:           
            sorted_dict_temp = tiebreaker(list_team)
            for team in sorted_dict_temp:                           
                dict_up_position[team[0]][str(positon)][0] += 1
                dict_up_position[team[0]][str(positon)][1].add(key)
                positon += 1
            return_dict += sorted_dict_temp          
    return return_dict

In [8]:
def transform_csv_2_dict(url):
    with open(url, mode='r', encoding='utf-8') as file:
        reader = csv.DictReader(file)
        data = []
        for row in reader:
            data.append({
                "UP": row["UP"], 
                "Team": row["Team"],
                "wins": int(row["wins"]),
                "matchDelta": int(row["matchDelta"]),
                "h2h": ast.literal_eval(row["h2h"])  
            })
    return data

In [9]:
test_set_dict = {}
for team in teamNameScores["name"]:
    test_set_dict[team] = {
        "1": [0,set()],
        "2": [0,set()],
        "3": [0,set()],
        "4": [0,set()],
        "5": [0,set()],
        "6": [0,set()],
        "7": [0,set()],
        "8": [0,set()],
        "9": [0,set()],
        "10": [0,set()],
        "11": [0,set()],
        "12": [0,set()],

    }

In [10]:
def process_batch(feed_path, result_path, matches, batch_size=512, output_file="result.csv", progress_file="progress.txt"): #Ojo que ouput result no se esta usando
    # Listar todos los archivos CSV en el directorio
    files_csv = [archivo for archivo in os.listdir(feed_path) if archivo.endswith(".csv")]

    try:
        os.mkdir(result_path)
        print(f"Directory '{result_path}' created successfully.")
    except FileExistsError:
        print(f"Directory '{result_path}' already exists.")
    except PermissionError:
        print(f"Permission denied: Unable to create '{result_path}'.")
    except Exception as e:
        print(f"An error occurred: {e}")

    for file in files_csv:
        file_path = os.path.join(feed_path, file)  
        print(f"Processing file: {file_path}")
        
        try:
            data = transform_csv_2_dict(file_path)
            file_output = os.path.join(result_path, f"processed_{file}")
            
            run_round_delta_with_resume(
                matches=matches,
                previous_results=data,
                batch_size=batch_size,
                output_file=file_output,
                progress_file=progress_file
            )
            
            print(f"File {file} processed and saved to {file_output}.")
        
        except Exception as e:
            print(f"Error processing file {file}: {e}")

In [11]:
teams = teamNameScores
matches = (("Kru","Lev"), ("100T","mibr"),("NRG","EG"), ("FUR","LOUD"),("2G","G2"),("C9","SEN"))
matches2 = (("Kru","100T"), ("Lev","mibr"),("NRG","FUR"), ("EG","LOUD"),("C9","G2"),("2G","SEN"))

In [12]:
#Process de fecha 1 (se pueden mejorar los paths)
previous_results = process_for_round(teams)
matches = (("Kru", "Lev"), ("100T", "mibr"), ("NRG", "EG"), ("FUR", "LOUD"), ("2G", "G2"), ("C9", "SEN"))
run_round_delta_with_resume(matches, previous_results=previous_results, batch_size=512, output_file=".//results//results_batch_test", progress_file=".//results//progress//progress1.txt")

Lote 1/9 procesado y guardado.
Lote 2/9 procesado y guardado.
Lote 3/9 procesado y guardado.
Lote 4/9 procesado y guardado.
Lote 5/9 procesado y guardado.
Lote 6/9 procesado y guardado.
Lote 7/9 procesado y guardado.
Lote 8/9 procesado y guardado.
Lote 9/9 procesado y guardado.
Procesamiento completado.


In [13]:
#Aca va match2
feed_path = './/results'
path_results = './/results//fecha_2'

process_batch(feed_path,path_results, matches2, batch_size=512,output_file="result_test.csv",progress_file="progress.txt")

Directory './/results//fecha_2' already exists.
Processing file: .//results\results_batch_test0.csv


KeyboardInterrupt: 

In [14]:
#procesar lote de resultados: 
csv_to_process = './/results//fecha_2'

files_csv = [archivo for archivo in os.listdir(csv_to_process) if archivo.endswith(".csv")]

In [15]:
test_set_dict

{'Kru': {'1': [0, set()],
  '2': [0, set()],
  '3': [0, set()],
  '4': [0, set()],
  '5': [0, set()],
  '6': [0, set()],
  '7': [0, set()],
  '8': [0, set()],
  '9': [0, set()],
  '10': [0, set()],
  '11': [0, set()],
  '12': [0, set()]},
 'Lev': {'1': [0, set()],
  '2': [0, set()],
  '3': [0, set()],
  '4': [0, set()],
  '5': [0, set()],
  '6': [0, set()],
  '7': [0, set()],
  '8': [0, set()],
  '9': [0, set()],
  '10': [0, set()],
  '11': [0, set()],
  '12': [0, set()]},
 '100T': {'1': [0, set()],
  '2': [0, set()],
  '3': [0, set()],
  '4': [0, set()],
  '5': [0, set()],
  '6': [0, set()],
  '7': [0, set()],
  '8': [0, set()],
  '9': [0, set()],
  '10': [0, set()],
  '11': [0, set()],
  '12': [0, set()]},
 'mibr': {'1': [0, set()],
  '2': [0, set()],
  '3': [0, set()],
  '4': [0, set()],
  '5': [0, set()],
  '6': [0, set()],
  '7': [0, set()],
  '8': [0, set()],
  '9': [0, set()],
  '10': [0, set()],
  '11': [0, set()],
  '12': [0, set()]},
 'NRG': {'1': [0, set()],
  '2': [0, set()

In [16]:
for file in files_csv[:2]:
    file_path = csv_to_process + '//' + file
    data = transform_csv_2_dict(file_path)
    grouped_data = groupby_UP(data)
    dict_ready_to_sorot = heriarchy_dict_for_sort(grouped_data)
    for key in dict_ready_to_sorot.keys():
        sorted_dict = sort_dict_by_wins(dict_ready_to_sorot[key])
        untie_round_save(sorted_dict,test_set_dict,key)

Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff needed
Round diff

In [17]:
len(test_set_dict['Kru']['4'][1])

81920

In [42]:
(test_set_dict['2G']['4'][0])

106496

In [18]:
#Creo que esto no haace falta en los test
path_file = csv_to_process + '//' + files_csv[0]
data = transform_csv_2_dict(path_file)

In [19]:
groupby_up = groupby_UP(data)

In [20]:
dict_ready_to_sort = heriarchy_dict_for_sort(groupby_up)

In [21]:
dict_ready_to_sort

{'1-0-(0, 0, 0, 0, 0, 0)-0-(0, 0, 0, 0, 0, 0)': {'Kru': {'wins': 6,
   'matchDelta': 1,
   'h2h': ['FUR', 'mibr', 'EG', 'LOUD', 'C9', 'SEN']},
  'Lev': {'wins': 10,
   'matchDelta': 15,
   'h2h': ['SEN', 'NRG', 'G2', '100T', 'EG', 'LOUD', 'FUR', 'Kru']},
  '100T': {'wins': 6, 'matchDelta': 1, 'h2h': ['EG', 'G2', 'NRG', 'Kru']},
  'mibr': {'wins': 3, 'matchDelta': -11, 'h2h': ['EG', '100T', 'Lev']},
  'NRG': {'wins': 4, 'matchDelta': -7, 'h2h': ['Kru', 'LOUD', 'FUR', 'mibr']},
  'EG': {'wins': 5, 'matchDelta': -5, 'h2h': ['SEN', 'LOUD', 'NRG']},
  'FUR': {'wins': 4, 'matchDelta': -7, 'h2h': ['100T', 'mibr', 'NRG']},
  'LOUD': {'wins': 6,
   'matchDelta': 1,
   'h2h': ['SEN', 'G2', 'mibr', '100T', 'FUR', 'EG']},
  '2G': {'wins': 7,
   'matchDelta': 3,
   'h2h': ['FUR', 'EG', 'mibr', 'Kru', 'NRG', 'Kru', 'SEN']},
  'G2': {'wins': 2, 'matchDelta': 4, 'h2h': ['2G', 'C9']},
  'C9': {'wins': 6,
   'matchDelta': -4,
   'h2h': ['Lev', 'EG', 'LOUD', 'FUR', 'mibr', 'NRG']},
  'SEN': {'wins': 8,
 

In [22]:
def sort_dict_by_wins(single_up_round):
    #count = 1
    sorted_table = sorted(single_up_round.items(), key =lambda x: (x[1]["wins"], x[1]["matchDelta"]), reverse=True)
    
    grouped_table = group_table(sorted_table)
    
    #count += 1
    return grouped_table
#Aca tengo que agregar el desempate y los resultados y no crear todo la lista larga? 

In [23]:
def two_teams_tie(tie_teams):
    if len(tie_teams) != 2:
        print("not 2 tie teams")
    else:
        team1_h2h_vs_rival = set(tie_teams[0][1]["h2h"]) & set([tie_teams[1][0]])
        if len(team1_h2h_vs_rival) == 0:
            tie_teams = tie_teams[1:] + tie_teams[:1]

    return tie_teams

In [24]:
def three_way_tie(tie_teams):
    if len(tie_teams) != 3:
        print("not 3 way tie")
    else:
        teams = [x[0] for x in tie_teams]
        for index, team in enumerate(tie_teams):  # one team superiority vs the other 2
            team_h2h = set(tie_teams[index][1]["h2h"]) & set(teams)

            if len(team_h2h) == 2:
                pop_team = tie_teams.pop(index)
                remaining_tie = two_teams_tie(tie_teams)
                tie_teams = [pop_team] + remaining_tie

            elif index == 2:
                pass#print("Round diff needed")

    return tie_teams

In [25]:
def tiebreaker(tie_teams):
    amount_tie_teams = len(tie_teams)
    if amount_tie_teams >= 4:
        match_tie_set = set()
        for team in tie_teams: #This need to be check
            match_tie_set.add(team[1]["matchDelta"])  
        if amount_tie_teams != match_tie_set:
            pass 
        
    if amount_tie_teams == 3:
        tie_teams = three_way_tie(tie_teams)
        
    if amount_tie_teams == 2:  # Esto se puede cambiar y modificar solo la posición
        
        tie_teams = two_teams_tie(tie_teams)
        
    return tie_teams or []

In [26]:
def untie(up_dict_sorted,dict_up_position):
    positon = 1
    return_dict = []
    for list_team in up_dict_sorted:
        if len(list_team) == 1:            
            dict_up_position[list_team[0][0]][str(positon)] += 1
            positon += 1
            return_dict += [list_team]
        if len(list_team) > 1:           
            sorted_dict_temp = tiebreaker(list_team)
            for team in sorted_dict_temp:             
                dict_up_position[team[0]][str(positon)] += 1
                positon += 1
            return_dict += sorted_dict_temp          
    return return_dict

In [29]:

def extract_parentheses_values(input_string):
    # Valores dentro de parentesis
    pattern = r'\((.*?)\)'
    matches = re.findall(pattern, input_string)
    # Convertir los grupos grupo capturado en una lista de enteros
    results = [list(map(int, match.split(','))) for match in matches]
    return results

In [30]:
def create_nested_dict(start, end):
    match_results = {}
    for i in range(start, end + 1):
        match_results[str(i)] = {str(j): [] for j in range(6)}
    return match_results

# Crear el diccionario desde 1 hasta 10 como ejemplo
nested_dict = create_nested_dict(1, 4)


{'1': {'0': [], '1': [], '2': [], '3': [], '4': [], '5': []}, '2': {'0': [], '1': [], '2': [], '3': [], '4': [], '5': []}, '3': {'0': [], '1': [], '2': [], '3': [], '4': [], '5': []}, '4': {'0': [], '1': [], '2': [], '3': [], '4': [], '5': []}}


In [105]:
#Probablemente aca me conviene pasar a sql, armar la base de datos y trabajarla desde sql directo
#Checkear que es mas rapido, correr 2 veces el for con un extracted element particular o el enumarte de extracted_element + mas el otro for
#El enumarated(extracted_element) con el for evaluando los 0 1 es mas escalable 

def create_position_dicts(team, position_set_dict,nested_dict_range=[1,4]):
    result_mapping = {
        0: '0-2',
        1: '1-2',
        2: '2-1',
        3: '2-0',
    }
    nested_dict = create_nested_dict(nested_dict_range[0], nested_dict_range[1])
    nested_dict_match2 = create_nested_dict(nested_dict_range[0], nested_dict_range[1])
    for position in position_set_dict[team]:
        if int(position) < 5:
            for element in position_set_dict[team][position][1]:
                extracted_element = extract_parentheses_values(element)
                for number, result in enumerate(extracted_element[0]): 
                    nested_dict[str(position)][str(number)].append(
                        (matches[number][0], result_mapping[result], matches[number][1])
                    )
                for number, result in enumerate(extracted_element[1]):
                    nested_dict_match2[str(position)][str(number)].append(
                        (matches2[number][0], result_mapping[result], matches2[number][1])
                    )
    return nested_dict, nested_dict_match2

In [121]:
def df_with_positions(weeek1,week2):
    postion = ['position']
    week1columns = ['week1_match_1','week1_match_2','week1_match_3','week1_match_4','week1_match_5','week1_match_6']
    week2columns = ['week2_match_1','week2_match_2','week2_match_3','week2_match_4','week2_match_5','week2_match_6']

    columns_df = postion + week1columns + week2columns

    df_base = pd.DataFrame(columns=columns_df)

    for key in weeek1.keys():    
        df_week1 = pd.DataFrame.from_dict(weeek1[key])
        df_week1.columns = ['week1_match_1','week1_match_2','week1_match_3','week1_match_4','week1_match_5','week1_match_6']

        df_week2 = pd.DataFrame.from_dict(week2[key])
        df_week2.columns = ['week2_match_1','week2_match_2','week2_match_3','week2_match_4','week2_match_5','week2_match_6']

        df_combined = pd.concat([df_week1, df_week2], axis=1)
        df_combined['position'] = key

        df_base = pd.concat([df_base,df_combined],ignore_index=True)
    return df_combined

In [120]:
week1_dict_to_df, week2_dict_to_df = create_position_dicts('2G',test_set_dict,[1,4])

In [122]:
df_g2 = df_with_positions(week1_dict_to_df,week2_dict_to_df)

In [123]:
df_g2

week1_match_1      week1_match_2   week1_match_3     week1_match_4  \
0      (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 0-2, EG)  (FUR, 1-2, LOUD)   
1      (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 1-2, EG)  (FUR, 0-2, LOUD)   
2      (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 1-2, EG)  (FUR, 0-2, LOUD)   
3      (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 1-2, EG)  (FUR, 2-0, LOUD)   
4      (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 0-2, EG)  (FUR, 0-2, LOUD)   
...                ...                ...             ...               ...   
53243  (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 2-1, EG)  (FUR, 2-1, LOUD)   
53244  (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 2-1, EG)  (FUR, 0-2, LOUD)   
53245  (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 1-2, EG)  (FUR, 0-2, LOUD)   
53246  (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 2-0, EG)  (FUR, 1-2, LOUD)   
53247  (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 0-2, EG)  (FUR, 1-2, LOUD)   

       week1_match_5   week1_match_6     week2_match_1     week2_match_2  \
0      (2G, 0-2, G2)  (C9, 2-1, SEN)  (Kru, 0-2, 100T)  (Lev, 1-2, mibr)   
1      (2G, 1-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)  (Lev, 1-2, mibr)   
2      (2G, 1-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)  (Lev, 1-2, mibr)   
3      (2G, 1-2, G2)  (C9, 0-2, SEN)  (Kru, 0-2, 100T)  (Lev, 1-2, mibr)   
4      (2G, 1-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)  (Lev, 2-1, mibr)   
...              ...             ...               ...               ...   
53243  (2G, 0-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)  (Lev, 2-1, mibr)   
53244  (2G, 1-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)  (Lev, 0-2, mibr)   
53245  (2G, 0-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)  (Lev, 2-0, mibr)   
53246  (2G, 0-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)  (Lev, 0-2, mibr)   
53247  (2G, 1-2, G2)  (C9, 2-1, SEN)  (Kru, 0-2, 100T)  (Lev, 2-0, mibr)   

         week2_match_3    week2_match_4  week2_match_5   week2_match_6  \
0      (NRG, 2-1, FUR)  (EG, 2-1, LOUD)  (C9, 2-0, G2)  (2G, 0-2, SEN)   
1      (NRG, 0-2, FUR)  (EG, 1-2, LOUD)  (C9, 2-1, G2)  (2G, 0-2, SEN)   
2      (NRG, 0-2, FUR)  (EG, 0-2, LOUD)  (C9, 2-1, G2)  (2G, 1-2, SEN)   
3      (NRG, 0-2, FUR)  (EG, 0-2, LOUD)  (C9, 2-1, G2)  (2G, 0-2, SEN)   
4      (NRG, 2-0, FUR)  (EG, 0-2, LOUD)  (C9, 2-0, G2)  (2G, 0-2, SEN)   
...                ...              ...            ...             ...   
53243  (NRG, 2-1, FUR)  (EG, 0-2, LOUD)  (C9, 2-1, G2)  (2G, 0-2, SEN)   
53244  (NRG, 0-2, FUR)  (EG, 2-0, LOUD)  (C9, 2-0, G2)  (2G, 0-2, SEN)   
53245  (NRG, 1-2, FUR)  (EG, 2-0, LOUD)  (C9, 2-0, G2)  (2G, 0-2, SEN)   
53246  (NRG, 2-1, FUR)  (EG, 0-2, LOUD)  (C9, 2-1, G2)  (2G, 1-2, SEN)   
53247  (NRG, 0-2, FUR)  (EG, 1-2, LOUD)  (C9, 2-0, G2)  (2G, 0-2, SEN)   

      position  
0            4  
1            4  
2            4  
3            4  
4            4  
...        ...  
53243        4  
53244        4  
53245        4  
53246        4  
53247        4  

[53248 rows x 13 columns]

In [107]:
postion = ['position']
week1columns = ['week1_match_1','week1_match_2','week1_match_3','week1_match_4','week1_match_5','week1_match_6']
week2columns = ['week2_match_1','week2_match_2','week2_match_3','week2_match_4','week2_match_5','week2_match_6']

columns_df = postion + week1columns + week2columns

df_base = pd.DataFrame(columns=columns_df)


In [108]:
for key in nested_dict.keys():    
    df_week1 = pd.DataFrame.from_dict(test1[key])
    df_week1.columns = ['week1_match_1','week1_match_2','week1_match_3','week1_match_4','week1_match_5','week1_match_6']

    df_week2 = pd.DataFrame.from_dict(test2[key])
    df_week2.columns = ['week2_match_1','week2_match_2','week2_match_3','week2_match_4','week2_match_5','week2_match_6']

    df_combined = pd.concat([df_week1, df_week2], axis=1)
    df_combined['position'] = key
    print(key)
    df_base = pd.concat([df_base,df_combined],ignore_index=True)

1
2
3
4


In [117]:
(test_set_dict['2G']['2'][0])
(test_set_dict['2G']['3'][0])

299008

In [118]:
test_set_dict['2G']['2'][0] + test_set_dict['2G']['3'][0] + test_set_dict['2G']['4'][0]

524288

In [103]:
df_base['position'].unique()

array(['2', '3', '4'], dtype=object)

In [119]:
df_base

position    week1_match_1      week1_match_2   week1_match_3  \
0             2  (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 1-2, EG)   
1             2  (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 0-2, EG)   
2             2  (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 2-0, EG)   
3             2  (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 2-0, EG)   
4             2  (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 2-0, EG)   
...         ...              ...                ...             ...   
524283        4  (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 2-1, EG)   
524284        4  (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 2-1, EG)   
524285        4  (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 1-2, EG)   
524286        4  (Kru, 0-2, Lev)  (100T, 0-2, mibr)  (NRG, 2-0, EG)   
524287        4  (Kru, 0-2, Lev)  (100T, 1-2, mibr)  (NRG, 0-2, EG)   

           week1_match_4  week1_match_5   week1_match_6     week2_match_1  \
0       (FUR, 2-1, LOUD)  (2G, 2-1, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)   
1       (FUR, 2-1, LOUD)  (2G, 2-0, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)   
2       (FUR, 2-1, LOUD)  (2G, 1-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)   
3       (FUR, 2-1, LOUD)  (2G, 2-1, G2)  (C9, 2-0, SEN)  (Kru, 0-2, 100T)   
4       (FUR, 0-2, LOUD)  (2G, 0-2, G2)  (C9, 2-0, SEN)  (Kru, 0-2, 100T)   
...                  ...            ...             ...               ...   
524283  (FUR, 2-1, LOUD)  (2G, 0-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)   
524284  (FUR, 0-2, LOUD)  (2G, 1-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)   
524285  (FUR, 0-2, LOUD)  (2G, 0-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)   
524286  (FUR, 1-2, LOUD)  (2G, 0-2, G2)  (C9, 1-2, SEN)  (Kru, 0-2, 100T)   
524287  (FUR, 1-2, LOUD)  (2G, 1-2, G2)  (C9, 2-1, SEN)  (Kru, 0-2, 100T)   

           week2_match_2    week2_match_3    week2_match_4  week2_match_5  \
0       (Lev, 2-1, mibr)  (NRG, 2-1, FUR)  (EG, 2-1, LOUD)  (C9, 0-2, G2)   
1       (Lev, 1-2, mibr)  (NRG, 2-1, FUR)  (EG, 1-2, LOUD)  (C9, 0-2, G2)   
2       (Lev, 0-2, mibr)  (NRG, 0-2, FUR)  (EG, 1-2, LOUD)  (C9, 0-2, G2)   
3       (Lev, 1-2, mibr)  (NRG, 0-2, FUR)  (EG, 2-0, LOUD)  (C9, 0-2, G2)   
4       (Lev, 2-0, mibr)  (NRG, 2-0, FUR)  (EG, 2-1, LOUD)  (C9, 0-2, G2)   
...                  ...              ...              ...            ...   
524283  (Lev, 2-1, mibr)  (NRG, 2-1, FUR)  (EG, 0-2, LOUD)  (C9, 2-1, G2)   
524284  (Lev, 0-2, mibr)  (NRG, 0-2, FUR)  (EG, 2-0, LOUD)  (C9, 2-0, G2)   
524285  (Lev, 2-0, mibr)  (NRG, 1-2, FUR)  (EG, 2-0, LOUD)  (C9, 2-0, G2)   
524286  (Lev, 0-2, mibr)  (NRG, 2-1, FUR)  (EG, 0-2, LOUD)  (C9, 2-1, G2)   
524287  (Lev, 2-0, mibr)  (NRG, 0-2, FUR)  (EG, 1-2, LOUD)  (C9, 2-0, G2)   

         week2_match_6  
0       (2G, 2-0, SEN)  
1       (2G, 2-0, SEN)  
2       (2G, 2-0, SEN)  
3       (2G, 2-0, SEN)  
4       (2G, 2-1, SEN)  
...                ...  
524283  (2G, 0-2, SEN)  
524284  (2G, 0-2, SEN)  
524285  (2G, 0-2, SEN)  
524286  (2G, 1-2, SEN)  
524287  (2G, 0-2, SEN)  

[524288 rows x 13 columns]